## Sequence Learning Trainer

This one uses a generator and discriminator with sequence learning capabilities in the form of LSTM and/or GRU layers. This allows the raw audio data to be passed directly into the network without requiring so many input nodes that the whole thing crashes. It may slow down the propagation of a single entry to the point that it is no longer feasible though as LSTM and GRU layers are quite slow to evaluate or train.

In [13]:
#Imports, I've switched from Librosa to scipy for performance
#import librosa
from scipy.io.wavfile import read as wavread
import os
import numpy as np
import IPython.display as ipd

#Sets path to music files
#For Windows
#path = os.getcwd()+'\\EDM_Wav\\'
#For Linux
path = os.getcwd()+'/EDM_WAV/'

#Loads music
songlist = []
#This is loading in a sample song to get the sampling rate

#For Windows
#sr,test_song = wavread(path+'5061 Philippe Van Mullem - Canopy (Progress Mix).wav')

#For Linux (using the weird ffmpeg commandline conversion)
sr,test_song = wavread(path+'99806_Silencer_-_Drown_In_Me_feat._Berwitz_(Force_Mass_Motions_Stadium_JKT_Mix).mp3.wav')
songnames = os.listdir(path)


#Loop over and load all of the songs
for i in range(20):#range(int((len(songnames)*3)/4)):
    #This only grabs the left channel for now on Windows
    #songlist.append(wavread(path+songnames[i])[1][:,0])
    #On Linux I converted it to Mono
    songlist.append(wavread(path+songnames[i])[1])

In [14]:
#This is how a song has to be played
ipd.Audio(songlist[0].T,rate=sr)

In [15]:
#This is only necessary if the songs are of different lengths
#Even songs that seem very close can still differ by a few samples
#So this is probably worth running

#Pads the shorter songs with zeros
#####################################
#Finds the longest song
maxlength = 0
for i in songlist:
    if (len(i)>maxlength):
        maxlength = len(i)

#Pads the songs
for i in range(len(songlist)):
    songlist[i] = np.append(songlist[i],np.zeros(maxlength-len(songlist[i])))


In [38]:
#Transforming data to be input into an LSTM layer
songarray = np.array(songlist)
songarray = songarray.reshape((len(songlist),len(songlist[0]),1))
#Generating random data to test the discriminator at first
fakearray = np.random.rand(len(songlist),len(songlist[0]),1)
#Generating labels for the discriminator
y = np.hstack([np.ones([1,len(songlist)]),np.zeros([1,len(songlist)])])

#Compiling the two arrays

inputarray = np.vstack([songarray,fakearray])

# GAN Trainer
## Discriminator

In [ ]:
#Neural network imports
from tensorflow.keras.models import Sequential
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.layers import Dense, LSTM

#Define the discriminator
Dsc = Sequential()
Dsc.add(LSTM(150,input_shape=(len(songlist[0]),1),activation='relu'))
Dsc.add(Dense(8,activation='relu'))
Dsc.add(Dense(1,activation='sigmoid'))
Dsc.compile(loss='binary_crossentropy',optimizer='adam',metrics=['accuracy'])

Dsc.fit(inputarray,y.T)


Train on 40 samples


## Generator

In [ ]:
#Define the generator

#Selecting how many input nodes it has, it will get downscaled to the appropriate size
input_nodes = 1500

Gen = Sequential()
Gen.add(Dense(input_nodes,input_dim=input_nodes,activation='relu'))
Gen.add(Dense(3000,activation='relu'))
Gen.add(Dense(2500,activation='relu'))
Gen.add(Dense(500,activation='relu'))
Gen.add(Dense(n_components,activation='relu'))


In [ ]:
#Here the GAN is defined.
#In order to merge the generator and discriminator, a virtual third model is created

#Make the descriminator not trainable here so that only the generator is trained in the virtual model
#This still allows the discriminator to be trained on its own since it has already been compiled above
Dsc.trainable = False

GAN = Sequential()
#Add generator
GAN.add(Gen)
#Add Discriminator
GAN.add(Dsc)
#Compile GAN
GAN.compile(optimizer='adam',loss='binary_crossentropy',metrics=['accuracy'])

In [ ]:
#Finally, training

#First train the discriminator

#Generate fake songs
fake_songs = Gen.predict(np.array(np.random.rand(len(songlist),input_nodes)))
y = np.concatenate([np.ones(len(songlist)),np.zeros(len(songlist))])
x = np.concatenate([songs_pca,fake_songs])

#Shuffle the order of the songs
indices = np.arange(len(y))
np.random.shuffle(indices)
x = x[indices]
y = y[indices]

Dsc.fit(x,y,epochs = 10)